# Extract SrcTables Results in  OGA

 work with Weakly_2024_07
- use jupyter kernel LSST
- author : Sylvie Dagoret-Campagne
- affiliation : IJCLab
- creation date : 2024/02/18
- update : 2024/02/23


Try to find raw sources


In [1]:
! eups list -s | grep LOCAL

analysis_tools        LOCAL:/home/d/dagoret/repos/repos_w_2024_07/analysis_tools 	setup
atmospec              LOCAL:/home/d/dagoret/repos/repos_w_2024_07/atmospec 	setup
eups                  LOCAL:/opt/lsst/software/stack/conda/miniconda3-py38_4.9.2/envs/lsst-scipipe-8.0.0/eups 	setup
spectractor           LOCAL:/home/d/dagoret/repos/repos_w_2024_07/Spectractor 	setup


In [2]:
! eups list -s lsst_distrib

   g4213664e8e+34187316c4 	current w_2024_07 setup


In [3]:
import lsst.daf.butler as dafButler
#import lsst.summit.utils.butlerUtils as butlerUtils

In [4]:
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
from mpl_toolkits.axes_grid1 import make_axes_locatable
from matplotlib.colors import LogNorm,SymLogNorm


import matplotlib.ticker                         # here's where the formatter is
from matplotlib.ticker import (MultipleLocator, FormatStrFormatter,
                               AutoMinorLocator)

from astropy.visualization import (MinMaxInterval, SqrtStretch,ZScaleInterval,PercentileInterval,
                                   ImageNormalize,imshow_norm)
from astropy.visualization.stretch import SinhStretch, LinearStretch,AsinhStretch,LogStretch

from astropy.io import fits
from astropy.table import Table
import pandas as pd

import matplotlib.ticker                         # here's where the formatter is
import os
import re
import pandas as pd

plt.rcParams["figure.figsize"] = (4,3)
plt.rcParams["axes.labelsize"] = 'xx-large'
plt.rcParams['axes.titlesize'] = 'xx-large'
plt.rcParams['xtick.labelsize']= 'xx-large'
plt.rcParams['ytick.labelsize']= 'xx-large'

In [5]:
from matplotlib.ticker import (MultipleLocator, FormatStrFormatter,
                               AutoMinorLocator)

from astropy.visualization import (MinMaxInterval, SqrtStretch,ZScaleInterval,PercentileInterval,
                                   ImageNormalize,imshow_norm)
from astropy.visualization.stretch import SinhStretch, LinearStretch,AsinhStretch,LogStretch

from astropy.time import Time


In [6]:
# LSST Display
import lsst.afw.display as afwDisplay
afwDisplay.setDefaultBackend('matplotlib')

In [7]:
transform = AsinhStretch() + PercentileInterval(99.)

In [8]:
pd.options.display.max_columns = None
#pd.options.display.max_rows = None



## Configuration

In [9]:
DATE = 202402
#filesource_out="finalized_src_table_202402.csv"
#filetractpatch_out = 'Latiss_tractspatchs_202312.pickle'

In [10]:
#repo =  "/sdf/group/rubin/repo/main"
repo = "/sdf/group/rubin/repo/oga/"
butler = dafButler.Butler(repo)
registry = butler.registry

In [11]:
#file_out="sourceTable_202312.csv"

## Give the collection

In [12]:
#my_collection = "LATISS/runs/AUXTEL_DRP_IMAGING_2023-11A-10A-09AB-08ABC-07AB-05AB/w_2023_46/PREOPS-4553"
my_collection = "LATISS/runs/AUXTEL_DRP_IMAGING_20230509_20240201/w_2024_05/PREOPS-4871"

## Config

# Sources

In [13]:
# src : a Source catalog
# srcMatchFull
# finalized_src_table : sape of a pandas dataframe
data_product = "finalized_src_table" 
datasetRefs = butler.registry.queryDatasets(datasetType=data_product, collections=my_collection, where= "instrument='LATISS'")
filesource_out=f"{data_product}_{DATE}.csv"

In [14]:
all_ref_for_src = []
all_dataId = []
all_src = []
all_exposures = []
all_sourcesTables = []
all_dateobs = []

for i, ref in enumerate(datasetRefs):
    all_ref_for_src.append(ref.dataId)
    print(f"========================datasetType = {data_product} ============================================")
    print("fullId..................:",ref.dataId.full)
    print("visit...................:",ref.dataId["visit"])
    print("band....................:",ref.dataId["band"])
    print("physical filter.........:",ref.dataId["physical_filter"])
    print("run.....................:",ref.run)
   
    the_visit = ref.dataId["visit"]
    the_exposure = the_visit
    the_day_obs = ref.dataId["visit"]//100_000
    the_seq_num = ref.dataId["visit"]- the_day_obs*100_000    
    the_dataId = {'day_obs': the_day_obs,'seq_num':the_seq_num,'detector':0,}
    
    # extract time
    raw_img= butler.get('raw', dataId={'exposure': the_visit, 'instrument': 'LATISS', 'detector': 0}, collections = 'LATISS/raw/all')
    meta = raw_img.getMetadata()
    md = meta.toDict()
    date_obs = md['DATE-OBS']
    
    print(the_dataId)
    df_tab =  butler.get(ref,collections=my_collection)

    if not isinstance(df_tab, pd.DataFrame):
        print("Not a pandas Dataframe")
   
   
    N=len(df_tab)
    df_tab['visid_idx']= (i*np.ones(N)).astype(int)
   
    df_tab['dateobs']= (pd.to_datetime(date_obs))
    df_tab['mjd'] = Time(date_obs).mjd
    df_tab['seq_num'] = the_seq_num
    
    all_sourcesTables.append(df_tab) 
    all_dataId.append(the_dataId) 
    all_dateobs.append(date_obs)
    #print(df_tab)
    
 
    
    #registry_query = f"instrument='LATISS' and instrument=0 and visit={the_visit}]"
    #print(f"registry_query = {registry_query}")
    #info = registry.queryDimensionRecords('exposure',where = registry_query)
    
    #if i > 1:
    #    break

========================datasetType = finalized_src_table ============================================
fullId..................: {instrument: 'LATISS', visit: 2023051100262, band: 'r', physical_filter: 'SDSSr_65mm~empty'}
visit...................: 2023051100262
band....................: r
physical filter.........: SDSSr_65mm~empty
run.....................: LATISS/runs/AUXTEL_DRP_IMAGING_20230509_20240201/w_2024_05/PREOPS-4871/20240207T000014Z


/tmp/ipykernel_24978/3780976038.py:11: FutureWarning: Call to deprecated function (or staticmethod) full. (DataCoordinate.full is deprecated in favor of .mapping, and will be dropped after v27.) -- Deprecated since version v27.
  print("fullId..................:",ref.dataId.full)


{'day_obs': 20230511, 'seq_num': 262, 'detector': 0}


/tmp/ipykernel_24978/3780976038.py:30: UserWarning: Collections should not be specified with DatasetRef
  df_tab =  butler.get(ref,collections=my_collection)


========================datasetType = finalized_src_table ============================================
fullId..................: {instrument: 'LATISS', visit: 2023051100263, band: 'g', physical_filter: 'SDSSg_65mm~empty'}
visit...................: 2023051100263
band....................: g
physical filter.........: SDSSg_65mm~empty
run.....................: LATISS/runs/AUXTEL_DRP_IMAGING_20230509_20240201/w_2024_05/PREOPS-4871/20240207T000014Z


...

/tmp/ipykernel_24978/3780976038.py:30: UserWarning: Collections should not be specified with DatasetRef
  df_tab =  butler.get(ref,collections=my_collection)
/tmp/ipykernel_24978/3780976038.py:11: FutureWarning: Call to deprecated function (or staticmethod) full. (DataCoordinate.full is deprecated in favor of .mapping, and will be dropped after v27.) -- Deprecated since version v27.
  print("fullId..................:",ref.dataId.full)


{'day_obs': 20240130, 'seq_num': 169, 'detector': 0}
========================datasetType = finalized_src_table ============================================
fullId..................: {instrument: 'LATISS', visit: 2024013000170, band: 'y', physical_filter: 'empty~SDSSy_65mm'}
visit...................: 2024013000170
band....................: y
physical filter.........: empty~SDSSy_65mm
run.....................: LATISS/runs/AUXTEL_DRP_IMAGING_20230509_20240201/w_2024_05/PREOPS-4871/20240207T000014Z


/tmp/ipykernel_24978/3780976038.py:30: UserWarning: Collections should not be specified with DatasetRef
  df_tab =  butler.get(ref,collections=my_collection)
/tmp/ipykernel_24978/3780976038.py:11: FutureWarning: Call to deprecated function (or staticmethod) full. (DataCoordinate.full is deprecated in favor of .mapping, and will be dropped after v27.) -- Deprecated since version v27.
  print("fullId..................:",ref.dataId.full)


{'day_obs': 20240130, 'seq_num': 170, 'detector': 0}


/tmp/ipykernel_24978/3780976038.py:30: UserWarning: Collections should not be specified with DatasetRef
  df_tab =  butler.get(ref,collections=my_collection)


In [15]:
ref.expanded

<bound method DatasetRef.expanded of DatasetRef(DatasetType('finalized_src_table', {band, instrument, physical_filter, visit}, DataFrame), {instrument: 'LATISS', visit: 2024013000170, band: 'y', physical_filter: 'empty~SDSSy_65mm'}, run='LATISS/runs/AUXTEL_DRP_IMAGING_20230509_20240201/w_2024_05/PREOPS-4871/20240207T000014Z', id=035a3978-14f0-4c27-ad85-4cc315a40c3a)>

In [16]:
#df_tab

In [17]:
#t = Table.from_pandas(df_tab)

In [18]:
len(all_sourcesTables)

4041

In [19]:
#all_sourcesTables[0]

In [20]:
df=pd.concat(all_sourcesTables)

In [21]:
df

id  coord_ra  coord_dec  parent  base_SdssCentroid_x  \
0   171629648369680389  4.188138  -0.420736       0          1252.940701   
1   171629648369680398  4.188799  -0.420120       0          3094.767924   
2   171629648369680412  4.187863  -0.420638       0           956.014360   
3   171629648369680415  4.188575  -0.420112       0          2756.022290   
4   171629648369680422  4.187962  -0.420457       0          1349.255411   
..                 ...       ...        ...     ...                  ...   
43  180918223816884488  2.139401  -0.630450       0          3815.315103   
44  180918223816884495  2.139008  -0.630414       0          3131.854365   
45  180918223816884502  2.137818  -0.630399       0          1060.242005   
46  180918223816884503  2.137613  -0.630398       0           703.598013   
47  180918223816884504  2.138259  -0.630389       0          1829.109610   

    slot_Centroid_x  base_SdssCentroid_y  slot_Centroid_y  \
0       1252.940701           100.784131       100.784131   
1       3094.767924           352.706578       352.706578   
2        956.014360           598.228320       598.228320   
3       2756.022290           635.258340       635.258340   
4       1349.255411           787.207811       787.207811   
..              ...                  ...              ...   
43      3815.315103          3625.750825      3625.750825   
44      3131.854365          3712.362181      3712.362181   
45      1060.242005          3771.268966      3771.268966   
46       703.598013          3777.545579      3777.545579   
47      1829.109610          3783.049317      3783.049317   

    base_SdssCentroid_flag  base_GaussianFlux_flag_badCentroid  \
0                    False                               False   
1                    False                               False   
2                    False                               False   
3                    False                               False   
4                    False                               False   
..                     ...                                 ...   
43                   False                               False   
44                   False                               False   
45                   False                               False   
46                   False                               False   
47                   False                               False   

    base_PsfFlux_flag_badCentroid  \
0                           False   
1                           False   
2                           False   
3                           False   
4                           False   
..                            ...   
43                          False   
44                          False   
45                          False   
46                          False   
47                          False   

    ext_convolved_ConvolvedFlux_0_flag_badCentroid  \
0                                            False   
1                                            False   
2                                            False   
3                                            False   
4                                            False   
..                                             ...   
43                                           False   
44                                           False   
45                                           False   
46                                           False   
47                                           False   

    ext_convolved_ConvolvedFlux_1_flag_badCentroid  \
0                                            False   
1                                            False   
2                                            False   
3                                            False   
4                                            False   
..                                             ...   
43                                           False   
44                                           False   
4

In [22]:
df.to_csv(filesource_out)

In [23]:
print(df.columns.tolist())

['id', 'coord_ra', 'coord_dec', 'parent', 'base_SdssCentroid_x', 'slot_Centroid_x', 'base_SdssCentroid_y', 'slot_Centroid_y', 'base_SdssCentroid_flag', 'base_GaussianFlux_flag_badCentroid', 'base_PsfFlux_flag_badCentroid', 'ext_convolved_ConvolvedFlux_0_flag_badCentroid', 'ext_convolved_ConvolvedFlux_1_flag_badCentroid', 'ext_convolved_ConvolvedFlux_2_flag_badCentroid', 'ext_convolved_ConvolvedFlux_3_flag_badCentroid', 'ext_convolved_ConvolvedFlux_flag_badCentroid', 'ext_photometryKron_KronFlux_flag_badInitialCentroid', 'ext_shapeHSM_HsmPsfMoments_flag_badCentroid', 'ext_shapeHSM_HsmShapeRegauss_flag_badCentroid', 'ext_shapeHSM_HsmSourceMomentsRound_flag_badCentroid', 'ext_shapeHSM_HsmSourceMoments_flag_badCentroid', 'modelfit_DoubleShapeletPsfApprox_flag_badCentroid', 'slot_Centroid_flag', 'base_SdssCentroid_flag_edge', 'base_GaussianFlux_flag_badCentroid_edge', 'base_PsfFlux_flag_badCentroid_edge', 'ext_convolved_ConvolvedFlux_0_flag_badCentroid_edge', 'ext_convolved_ConvolvedFlux_1_

In [24]:
df['dateobs'].unique()

array(['2023-05-12T01:08:41.181000000', '2023-05-12T01:10:51.092000000',
       '2023-05-12T01:14:49.795000000', ...,
       '2024-01-31T04:16:34.256000000', '2024-01-31T04:17:18.333000000',
       '2024-01-31T04:18:06.855000000'], dtype='datetime64[ns]')